# InfluxDB Grundlagen

Bevor mit InfluxDB gearbeitet werden kann, muss als erstes die Client Library importiert werden.

In [6]:
from datetime import datetime

from influxdb_client import InfluxDBClient, Point, WritePrecision
from influxdb_client.client.write_api import SYNCHRONOUS

Im nächsten Schritt müssen die Verbindungsdaten angegeben werden. Ein API Token kann im InfluxDB Webinterface angelegt werden. Der Bucket wird automatisch erstellt. Es kann allerdings auch ein eigener Bucket verwendet werden.
Als URL muss darauf geachtet werden, die URL des Docker Containers zu nutzen, in dem die Datenbank ausgeführt wird. 

In [11]:
token = "8TYGzTJhqCyKpspMp95Yk858DY2uMzj6wbexbFGMiaLjcG6caiQtNiBKOFlxXnYuEoduFqS9o6_q8UmP1eJC0w=="
org = "test-org"
bucket = "test-bucked"
url = "http://influxdb:8086"

Jetzt wird der InfluxDB Client erstellt.

In [12]:
client = InfluxDBClient(
    url=url, 
    token=token,
    org=org
)     

## Daten in InfluxDB eintragen

Um Daten zu schreiben, wird ein Write Client genutzt. Dieser kann aus dem Client erstellt werden.

In [13]:
write_api = client.write_api(write_options=SYNCHRONOUS)

Zu guter Letzt kann dann ein Datenpunkt mit Demodaten hochgeladen werden.

In [14]:
p = Point("my_measurement").tag("location", "Prague").field("temperature", 25.3)
write_api.write(bucket=bucket, org=org, record=p)

# Daten aus InfluxDB abrufen

Ähnlich wie zum schreiben von Daten, wird für das Abrufen von Daten ein extra Query Client benötigt.

In [15]:
query_api = client.query_api()

Um die abzurufenden Daten festzulegen, wird ein Flux Querry erstellt.

In [16]:
query = 'from(bucket:"'+ bucket +'")\
|> range(start: -10m)\
|> filter(fn:(r) => r._measurement == "my_measurement")\
|> filter(fn: (r) => r.location == "Prague")\
|> filter(fn:(r) => r._field == "temperature" )'

Dieser Query kann dann mit dem Query Client ausgeführt werden.

In [17]:
result = query_api.query(org=org, query=query)

Mithilfe einer Schleife können die Datenpunkte jetzt durchgegangen werden. 

In [18]:
results = []
for table in result:
  for record in table.records:
    results.append((record.get_field(), record.get_value()))

print(results)

[('temperature', 25.3)]
